In [8]:
import torch

# Humandoid MARL
from Humanoid_MARL import envs
from Humanoid_MARL.envs.base_env import GymWrapper, VectorGymWrapper
from Humanoid_MARL.utils.torch_utils import save_models, load_models
from Humanoid_MARL.agent.ppo.train_torch import eval_unroll, get_agent_actions
from Humanoid_MARL.agent.ppo.agent import Agent
from Humanoid_MARL.envs.torch_wrapper import TorchWrapper
from IPython.display import HTML
from brax.io import html
import jax
from Humanoid_MARL import envs

In [9]:
config = {
        'num_timesteps': 100_000_000,
        'eval_frequency': 10,
        'episode_length': 1000,
        'unroll_length': 10,
        'num_minibatches': 32,
        'num_update_epochs': 8,
        'discounting': 0.97,
        'learning_rate': 3e-4,
        'entropy_cost': 1e-3,
        'num_envs': 2048,
        'batch_size': 512,
        'env_name': "humanoid",
        'render' : False,
        'device' : 'cuda',
        'model_path' : "../models/20240226_092325_ppo_humanoid_standing.pt",
        'video_length' : 300,
    }
env = envs.create(
        config['env_name'], batch_size=None, episode_length=config['episode_length'], backend="generalized"
    )
env = GymWrapper(env, get_jax_state=True)
env = TorchWrapper(env, device=config['device'], get_jax_state=True)

# env warmup
observation = env.reset()
action = torch.zeros(env.action_space.shape[0] * env.num_agents).to(config['device'])
env.step(action)
jax_states = []
num_steps = 1000
agents = load_models(config['model_path'], Agent, device=config['device'])

Models loaded from ../models/20240226_092325_ppo_humanoid_standing.pt


In [10]:
eval_reward = 0.0
episodes = torch.zeros((), device = config['device'])
for i in range(num_steps):
    print(f"{i} / {num_steps}")
    logits, action = get_agent_actions(agents, observation, env.obs_dims)
    jax_state, observation, reward, done, info = env.step(Agent.dist_postprocess(action[0]))
    episodes += torch.sum(done)
    jax_states.append(jax_state)
    print(f"{i} | {info} | DONE [{done}] | Reward [{reward}]")
    eval_reward += reward
print(f"Total Reward | {eval_reward / episodes}")

0 / 1000
0 | {'distance_from_origin': tensor(0.9249, device='cuda:0'), 'first_obs': tensor([ 1.3818e+00,  9.5108e-01, -2.5239e-02, -2.0876e-02,  4.1058e-02,
        -1.5037e-02, -1.1848e-03,  2.5091e-02, -1.0960e-02,  4.3684e-02,
        -3.9614e-02,  1.6623e-02, -3.0356e-02,  4.0333e-02,  3.6837e-02,
        -4.7539e-02, -6.2515e-03,  4.0049e-02,  2.8854e-02, -9.4651e-03,
         1.4689e-02, -2.7189e-02, -5.0537e-04,  2.4324e-02, -2.3594e-02,
         1.3918e-02,  1.2438e-02,  9.8313e-03, -5.9896e-03, -8.4448e-03,
        -2.2481e-02, -4.0195e-02,  4.1299e-02,  2.3473e-02, -4.4315e-02,
         3.0305e-02, -8.7707e-04, -2.7314e-02, -1.3433e-02,  4.2820e-02,
        -4.7953e-02,  2.8665e-02, -6.1042e-03,  3.6990e-03,  4.1291e-02,
         1.9976e+00,  6.1783e-03,  1.5167e-01,  6.1783e-03,  1.9890e+00,
        -5.9940e-02,  1.5167e-01, -5.9940e-02,  5.5291e-02,  8.9075e+00,
         8.4957e-02,  3.5706e-04,  1.2759e-02,  3.5706e-04,  8.1100e-02,
         7.3137e-04,  1.2759e-02,  7.313

In [11]:
HTML(html.render(env.sys, [jax_state.pipeline_state for jax_state in jax_states])) 

In [12]:
HTML(html.render(env.sys, [jax_state.pipeline_state for jax_state in jax_states])) 

: 